# Data Loading and Initial Exploration

Loads the dataset, checks basic properties, and assesses data quality.

In [1]:
%matplotlib inline
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.metrics import accuracy_score
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier
from sklearn.ensemble import StackingClassifier, VotingClassifier
from sklearn.linear_model import LogisticRegression
from imblearn.over_sampling import SMOTE
from sklearn.pipeline import make_pipeline
from sklearn.pipeline import Pipeline  # Import Pipeline
from sklearn.impute import SimpleImputer



import warnings
warnings.filterwarnings('ignore')



In [2]:
# Read the Dataset
df = pd.read_csv('../datasets/PCOS_data.csv')

#  Data Exploration and Cleaning

- Basic information about the dataset is printed, including data types and the presence of null values.
- Descriptive statistics are generated to understand the central tendency and distribution of the data.
- Column names are standardized by replacing spaces with underscores to facilitate easier data handling.

In [3]:
# Display basic information and the first few rows
print(df.info())
display(df.head())

# Generate descriptive statistics
display(df.describe())

# Check for missing values
print(df.isnull().sum())

# Normalize column names
df.columns = df.columns.str.strip().str.replace(' ', '_')
print(df.columns.tolist())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541 entries, 0 to 540
Data columns (total 44 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   Sl. No                  541 non-null    int64  
 1   Patient File No.        541 non-null    int64  
 2   PCOS (Y/N)              541 non-null    int64  
 3    Age (yrs)              541 non-null    int64  
 4   Weight (Kg)             541 non-null    float64
 5   Height(Cm)              541 non-null    float64
 6   BMI                     541 non-null    float64
 7   Blood Group             541 non-null    int64  
 8   Pulse rate(bpm)         541 non-null    int64  
 9   RR (breaths/min)        541 non-null    int64  
 10  Hb(g/dl)                541 non-null    float64
 11  Cycle(R/I)              541 non-null    int64  
 12  Cycle length(days)      541 non-null    int64  
 13  Marraige Status (Yrs)   540 non-null    float64
 14  Pregnant(Y/N)           541 non-null    in

Sl. No  Patient File No.  PCOS (Y/N)   Age (yrs)  Weight (Kg)  Height(Cm)   \
0       1                 1           0          28         44.6        152.0   
1       2                 2           0          36         65.0        161.5   
2       3                 3           1          33         68.8        165.0   
3       4                 4           0          37         65.0        148.0   
4       5                 5           0          25         52.0        161.0   

    BMI  Blood Group  Pulse rate(bpm)   RR (breaths/min)  ...  Pimples(Y/N)  \
0  19.3           15                78                22  ...             0   
1  24.9           15                74                20  ...             0   
2  25.3           11                72                18  ...             1   
3  29.7           13                72                20  ...             0   
4  20.1           11                72                18  ...             0   

   Fast food (Y/N)  Reg.Exercise(Y/N)  BP _Systolic (mmHg)  \
0              1.0                  0                  110   
1              0.0                  0                  120   
2              1.0                  0                  120   
3              0.0                  0                  120   
4              0.0                  0                  120   

   BP _Diastolic (mmHg)  Follicle No. (L)  Follicle No. (R)  \
0                    80                 3                 3   
1                    70                 3                 5   
2                    80                13                15   
3                    70                 2                 2   
4                    80                 3                 4   

  Avg. F size (L) (mm)  Avg. F size (R) (mm)  Endometrium (mm)  
0                 18.0                  18.0               8.5  
1                 15.0                  14.0               3.7  
2                 18.0                  20.0              10.0  
3                 15.0                  14.0               7.5  
4                 16.0                  14.0               7.0  

[5 rows x 44 columns]

Sl. No  Patient File No.  PCOS (Y/N)   Age (yrs)  Weight (Kg)  \
count  541.000000        541.000000  541.000000  541.000000   541.000000   
mean   271.000000        271.000000    0.327172   31.430684    59.637153   
std    156.317519        156.317519    0.469615    5.411006    11.028287   
min      1.000000          1.000000    0.000000   20.000000    31.000000   
25%    136.000000        136.000000    0.000000   28.000000    52.000000   
50%    271.000000        271.000000    0.000000   31.000000    59.000000   
75%    406.000000        406.000000    1.000000   35.000000    65.000000   
max    541.000000        541.000000    1.000000   48.000000   108.000000   

       Height(Cm)          BMI  Blood Group  Pulse rate(bpm)   \
count   541.000000  541.000000   541.000000        541.000000   
mean    156.484835   24.307579    13.802218         73.247689   
std       6.033545    4.055129     1.840812          4.430285   
min     137.000000   12.400000    11.000000         13.000000   
25%     152.000000   21.600000    13.000000         72.000000   
50%     156.000000   24.200000    14.000000         72.000000   
75%     160.000000   26.600000    15.000000         74.000000   
max     180.000000   38.900000    18.000000         82.000000   

       RR (breaths/min)  ...  Pimples(Y/N)  Fast food (Y/N)  \
count        541.000000  ...    541.000000       540.000000   
mean          19.243993  ...      0.489834         0.514815   
std            1.688629  ...      0.500359         0.500244   
min           16.000000  ...      0.000000         0.000000   
25%           18.000000  ...      0.000000         0.000000   
50%           18.000000  ...      0.000000         1.000000   
75%           20.000000  ...      1.000000         1.000000   
max           28.000000  ...      1.000000         1.000000   

       Reg.Exercise(Y/N)  BP _Systolic (mmHg)  BP _Diastolic (mmHg)  \
count         541.000000           541.000000            541.000000   
mean            0.247689           114.661738             76.927911   
std             0.432070             7.384556              5.574112   
min             0.000000            12.000000              8.000000   
25%             0.000000           110.000000             70.000000   
50%             0.000000           110.000000             80.000000   
75%             0.000000           120.000000             80.000000   
max             1.000000           140.000000            100.000000   

       Follicle No. (L)  Follicle No. (R)  Avg. F size (L) (mm)  \
count        541.000000        541.000000            541.000000   
mean           6.129390          6.641405             15.018115   
std            4.229294          4.436889              3.566839   
min            0.000000          0.000000              0.000000   
25%            3.000000          3.000000             13.000000   
50%            5.000000          6.000000             15.000000   
75%            9.000000         10.000000             18.000000   
max           22.000000         20.000000             24.000000   

       Avg. F size (R) (mm)  Endometrium (mm)  
count            541.000000        541.000000  
mean              15.451701          8.475915  
std                3.318848          2.165381  
min                0.000000          0.000000  
25%               13.000000          7.000000  
50%               16.000000          8.500000  
75%               18.000000          9.800000  
max               24.000000         18.000000  

[8 rows x 42 columns]

Sl. No                    0
Patient File No.          0
PCOS (Y/N)                0
 Age (yrs)                0
Weight (Kg)               0
Height(Cm)                0
BMI                       0
Blood Group               0
Pulse rate(bpm)           0
RR (breaths/min)          0
Hb(g/dl)                  0
Cycle(R/I)                0
Cycle length(days)        0
Marraige Status (Yrs)     1
Pregnant(Y/N)             0
No. of abortions          0
  I   beta-HCG(mIU/mL)    0
II    beta-HCG(mIU/mL)    0
FSH(mIU/mL)               0
LH(mIU/mL)                0
FSH/LH                    0
Hip(inch)                 0
Waist(inch)               0
Waist:Hip Ratio           0
TSH (mIU/L)               0
AMH(ng/mL)                0
PRL(ng/mL)                0
Vit D3 (ng/mL)            0
PRG(ng/mL)                0
RBS(mg/dl)                0
Weight gain(Y/N)          0
hair growth(Y/N)          0
Skin darkening (Y/N)      0
Hair loss(Y/N)            0
Pimples(Y/N)              0
Fast food (Y/N)     

- The script handles numeric columns by replacing non-numeric data and filling missing values with the median, which is robust against outliers.
- Categorical columns are processed by filling missing values with the mode.
- Additional feature engineering includes creating bins for BMI and age groups to capture more nuanced relationships in the data.

In [4]:
# Correctly handle numeric columns with special characters and potential non-numeric data
numeric_columns = ['BMI', 'Age_(yrs)', 'Weight_(Kg)', 'Waist:Hip_Ratio', 
                   'I___beta-HCG(mIU/mL)', 'II____beta-HCG(mIU/mL)', 
                   'FSH(mIU/mL)', 'LH(mIU/mL)', 'AMH(ng/mL)', 
                   'Cycle_length(days)', 'Endometrium_(mm)', 
                   'BP__Systolic_(mmHg)', 'BP__Diastolic_(mmHg)']

for col in numeric_columns:
    df[col] = pd.to_numeric(df[col].replace(r'^\.+$', '', regex=True), errors='coerce')
    df[col] = df[col].fillna(df[col].median())

# Handle categorical columns and fill missing values with mode
categorical_columns = ['PCOS_(Y/N)', 'Pregnant(Y/N)', 'Weight_gain(Y/N)', 
                       'hair_growth(Y/N)', 'Skin_darkening_(Y/N)', 
                       'Hair_loss(Y/N)', 'Pimples(Y/N)', 
                       'Fast_food_(Y/N)', 'Reg.Exercise(Y/N)', 
                       'Blood_Group']

for col in categorical_columns:
    df[col] = df[col].fillna(df[col].mode()[0])
    
    # Fill the single missing value in 'Marraige_Status_(Yrs)' with the median
df['Marraige_Status_(Yrs)'].fillna(df['Marraige_Status_(Yrs)'].median(), inplace=True)



In [5]:
# Encode categorical columns
labelencoder = LabelEncoder()
df[categorical_columns] = df[categorical_columns].apply(labelencoder.fit_transform)


In [6]:
# Scale all numeric columns
scaler = StandardScaler()
df[numeric_columns] = scaler.fit_transform(df[numeric_columns])

In [7]:
# Apply SMOTE for class balancing
X = df.drop('PCOS_(Y/N)', axis=1)
y = df['PCOS_(Y/N)']
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

In [8]:
# Display the resampled class distribution
print(f"Class distribution after SMOTE:\n{pd.Series(y_resampled).value_counts()}")

Class distribution after SMOTE:
PCOS_(Y/N)
0    364
1    364
Name: count, dtype: int64


In [9]:
# Example of clipping extreme outliers in Avg._F_size_(L)_(mm)
df['Avg._F_size_(L)_(mm)'] = df['Avg._F_size_(L)_(mm)'].clip(lower=-3, upper=3)


In [10]:
# Feature engineering for categorical binning
df['BMI_range'] = pd.cut(df['BMI'], bins=[0, 18.5, 24.9, 29.9, float('inf')], labels=[0, 1, 2, 3])
df['Age_group'] = pd.cut(df['Age_(yrs)'], bins=[0, 30, 40, 50, float('inf')], labels=[0, 1, 2, 3])


# Model Training 

In [11]:
# Prepare data for modeling
X = df.drop('PCOS_(Y/N)', axis=1)
y = df['PCOS_(Y/N)']

In [12]:
# Split the dataset
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)


In [13]:
# Define a pipeline for preprocessing (imputation + scaling)
pipeline = Pipeline([
    ('imputer', SimpleImputer(strategy='median')),  # Imputing missing values with median
    ('scaler', StandardScaler())                   # Standard scaling of features
])


In [14]:
# Apply the pipeline to both the training and test sets
X_train_preprocessed = pipeline.fit_transform(X_train)
X_test_preprocessed = pipeline.transform(X_test)

In [15]:
# Apply SMOTE only on the preprocessed training data
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X_train_preprocessed, y_train)


In [16]:
# Use the balanced (resampled) training data for model training
print(f"Class distribution after SMOTE:\n{pd.Series(y_resampled).value_counts()}")

# Check the shapes of the resampled and test sets to ensure consistency
print(f"Resampled training data shape: {X_resampled.shape}, {y_resampled.shape}")
print(f"Test data shape: {X_test_preprocessed.shape}, {y_test.shape}")

Class distribution after SMOTE:
PCOS_(Y/N)
0    291
1    291
Name: count, dtype: int64
Resampled training data shape: (582, 45), (582,)
Test data shape: (109, 45), (109,)


In [17]:
# Scale the features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

In [18]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.dummy import DummyClassifier
from sklearn.metrics import accuracy_score


In [19]:
# Reinitialize classifiers with the same configuration
classifiers = {
    'KNN (k=3)': KNeighborsClassifier(n_neighbors=3),
    'KNN (k=5)': KNeighborsClassifier(n_neighbors=5),
    'Decision Tree (gini)': DecisionTreeClassifier(criterion='gini'),
    'Decision Tree (entropy)': DecisionTreeClassifier(criterion='entropy'),
    'Random Forest': RandomForestClassifier(n_estimators=100, random_state=42),
    'Naive Bayes': GaussianNB(),
    'Dummy Classifier': DummyClassifier(strategy='most_frequent'),
    'XGBoost': XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=42),
    'LightGBM': LGBMClassifier(random_state=42),
    'CatBoost': CatBoostClassifier(verbose=0, random_state=42)
}


In [20]:
# Train and evaluate classifiers using the resampled training data and test set
results = {}
for name, clf in classifiers.items():
    clf.fit(X_resampled, y_resampled)  # Use resampled y_resampled for training
    y_pred = clf.predict(X_test_preprocessed)
    accuracy = accuracy_score(y_test, y_pred)
    results[name] = accuracy
    print(f'{name} - Accuracy: {accuracy:.4f}')

KNN (k=3) - Accuracy: 0.8624
KNN (k=5) - Accuracy: 0.8716
Decision Tree (gini) - Accuracy: 0.8440
Decision Tree (entropy) - Accuracy: 0.8532
Random Forest - Accuracy: 0.9266
Naive Bayes - Accuracy: 0.4128
Dummy Classifier - Accuracy: 0.6697
XGBoost - Accuracy: 0.9083
[LightGBM] [Info] Number of positive: 291, number of negative: 291
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000390 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3563
[LightGBM] [Info] Number of data points in the train set: 582, number of used features: 42
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

In [21]:
# Display the results
results_df = pd.DataFrame(list(results.items()), columns=['Classifier', 'Accuracy'])
print(results_df.sort_values(by='Accuracy', ascending=False))

                Classifier  Accuracy
4            Random Forest  0.926606
7                  XGBoost  0.908257
8                 LightGBM  0.908257
9                 CatBoost  0.899083
1                KNN (k=5)  0.871560
0                KNN (k=3)  0.862385
3  Decision Tree (entropy)  0.853211
2     Decision Tree (gini)  0.844037
6         Dummy Classifier  0.669725
5              Naive Bayes  0.412844


# Hyperparameter Tuning with optuna (Bayesian optimization)

- Decision Tree
- XGBoost
- LightGBM
- CatBoost

In [22]:
import optuna
from sklearn.model_selection import cross_val_score
from sklearn.tree import DecisionTreeClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier

In [23]:
# Define cross-validation method
from sklearn.model_selection import StratifiedKFold
cv = StratifiedKFold(n_splits=5)

In [24]:
# Decision Tree Tuning
def dt_objective(trial):
    params = {
        'criterion': trial.suggest_categorical('criterion', ['gini', 'entropy']),
        'max_depth': trial.suggest_int('max_depth', 3, 20),
        'min_samples_split': trial.suggest_int('min_samples_split', 2, 10),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 10),
    }
    dt = DecisionTreeClassifier(**params, random_state=42)
    score = cross_val_score(dt, X_train, y_train, cv=cv, scoring='accuracy').mean()
    return score

study_dt = optuna.create_study(direction='maximize')
study_dt.optimize(dt_objective, n_trials=50)
best_dt_params = study_dt.best_trial.params
print(f"Best Decision Tree params: {best_dt_params}")

[I 2024-10-15 16:44:41,959] A new study created in memory with name: no-name-8a17dc40-9b46-4059-836b-f466873b845a
[I 2024-10-15 16:44:41,979] Trial 0 finished with value: 0.8010692328254478 and parameters: {'criterion': 'entropy', 'max_depth': 15, 'min_samples_split': 7, 'min_samples_leaf': 3}. Best is trial 0 with value: 0.8010692328254478.
[I 2024-10-15 16:44:41,999] Trial 1 finished with value: 0.8055600106923283 and parameters: {'criterion': 'entropy', 'max_depth': 9, 'min_samples_split': 7, 'min_samples_leaf': 7}. Best is trial 1 with value: 0.8055600106923283.
[I 2024-10-15 16:44:42,012] Trial 2 finished with value: 0.8310344827586208 and parameters: {'criterion': 'gini', 'max_depth': 14, 'min_samples_split': 9, 'min_samples_leaf': 7}. Best is trial 2 with value: 0.8310344827586208.
[I 2024-10-15 16:44:42,035] Trial 3 finished with value: 0.8332531408714248 and parameters: {'criterion': 'gini', 'max_depth': 11, 'min_samples_split': 10, 'min_samples_leaf': 4}. Best is trial 3 with

Best Decision Tree params: {'criterion': 'gini', 'max_depth': 14, 'min_samples_split': 8, 'min_samples_leaf': 2}


In [25]:
# XGBoost Tuning
def xgb_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0)
    }
    xgb = XGBClassifier(**params, use_label_encoder=False, eval_metric='logloss', random_state=42)
    score = cross_val_score(xgb, X_train, y_train, cv=cv, scoring='accuracy').mean()
    return score

study_xgb = optuna.create_study(direction='maximize')
study_xgb.optimize(xgb_objective, n_trials=50)
best_xgb_params = study_xgb.best_trial.params
print(f"Best XGBoost params: {best_xgb_params}")

[I 2024-10-15 16:44:50,669] A new study created in memory with name: no-name-fa0534de-0542-4879-8ec1-c4222f2d5fe0
[I 2024-10-15 16:44:51,181] Trial 0 finished with value: 0.8726543704891739 and parameters: {'n_estimators': 349, 'max_depth': 8, 'learning_rate': 0.09704560461821723, 'subsample': 0.5393712191226601, 'colsample_bytree': 0.7936679857165185}. Best is trial 0 with value: 0.8726543704891739.
[I 2024-10-15 16:44:51,536] Trial 1 finished with value: 0.8773322641005079 and parameters: {'n_estimators': 283, 'max_depth': 4, 'learning_rate': 0.13322663718745945, 'subsample': 0.7262442449762929, 'colsample_bytree': 0.6963676636538845}. Best is trial 1 with value: 0.8773322641005079.
[I 2024-10-15 16:44:51,765] Trial 2 finished with value: 0.8726543704891739 and parameters: {'n_estimators': 183, 'max_depth': 3, 'learning_rate': 0.23864128518533162, 'subsample': 0.902162711672826, 'colsample_bytree': 0.9189422859748855}. Best is trial 1 with value: 0.8773322641005079.
[I 2024-10-15 16:

Best XGBoost params: {'n_estimators': 104, 'max_depth': 8, 'learning_rate': 0.07964927706635355, 'subsample': 0.6785595830548571, 'colsample_bytree': 0.654615031243744}


In [26]:
# LightGBM Tuning
def lgbm_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 150),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0)
    }
    lgbm = LGBMClassifier(**params, random_state=42)
    score = cross_val_score(lgbm, X_train, y_train, cv=cv, scoring='accuracy').mean()
    return score

study_lgbm = optuna.create_study(direction='maximize')
study_lgbm.optimize(lgbm_objective, n_trials=50)
best_lgbm_params = study_lgbm.best_trial.params
print(f"Best LightGBM params: {best_lgbm_params}")


[I 2024-10-15 16:45:10,873] A new study created in memory with name: no-name-e8ecb3c5-f06c-4982-83fb-6db5dda8e7c2
[I 2024-10-15 16:45:11,038] Trial 0 finished with value: 0.8727612937717188 and parameters: {'n_estimators': 193, 'max_depth': 8, 'learning_rate': 0.24804625448646214, 'num_leaves': 35, 'subsample': 0.6209137700715128}. Best is trial 0 with value: 0.8727612937717188.


[LightGBM] [Info] Number of positive: 113, number of negative: 232
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000157 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1667
[LightGBM] [Info] Number of data points in the train set: 345, number of used features: 44
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.327536 -> initscore=-0.719350
[LightGBM] [Info] Start training from score -0.719350
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes

[I 2024-10-15 16:45:11,383] Trial 1 finished with value: 0.8797113071371291 and parameters: {'n_estimators': 380, 'max_depth': 5, 'learning_rate': 0.08495476439871114, 'num_leaves': 130, 'subsample': 0.5510940414499939}. Best is trial 1 with value: 0.8797113071371291.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-10-15 16:45:11,634] Trial 2 finished with value: 0.875006682705159 and parameters: {'n_estimators': 448, 'max_depth': 3, 'learning_rate': 0.1353807196496994, 'num_leaves': 49, 'subsample': 0.9727846039303163}. Best is trial 1 with value: 0.8797113071371291.


...

[LightGBM] [Info] Number of positive: 113, number of negative: 233
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000228 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1657
[LightGBM] [Info] Number of data points in the train set: 346, number of used features: 44
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.326590 -> initscore=-0.723651
[LightGBM] [Info] Start training from score -0.723651
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes

[I 2024-10-15 16:45:22,298] Trial 48 finished with value: 0.8773322641005079 and parameters: {'n_estimators': 437, 'max_depth': 4, 'learning_rate': 0.28285288036972744, 'num_leaves': 69, 'subsample': 0.8979578483258785}. Best is trial 34 with value: 0.8936380646885859.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-10-15 16:45:22,714] Trial 49 finished with value: 0.8774926490243249 and parameters: {'n_estimators': 391, 'max_depth': 6, 'learning_rate': 0.03587003906756411, 'num_leaves': 79, 'subsample': 0.7741196686792948}. Best is trial 34 with value: 0.8936380646885859.


Best LightGBM params: {'n_estimators': 398, 'max_depth': 7, 'learning_rate': 0.2902257790086279, 'num_leaves': 94, 'subsample': 0.6003675054114488}


In [27]:
# CatBoost Tuning
def catboost_objective(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 100, 500),
        'depth': trial.suggest_int('depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-5, 10),
    }
    catboost = CatBoostClassifier(**params, verbose=0, random_state=42)
    score = cross_val_score(catboost, X_train, y_train, cv=cv, scoring='accuracy').mean()
    return score

study_catboost = optuna.create_study(direction='maximize')
study_catboost.optimize(catboost_objective, n_trials=50)
best_catboost_params = study_catboost.best_trial.params
print(f"Best CatBoost params: {best_catboost_params}")

[I 2024-10-15 16:45:38,657] A new study created in memory with name: no-name-63ee8df5-18f9-4060-ac3b-09b7260756f5
[I 2024-10-15 16:45:40,701] Trial 0 finished with value: 0.8842288158246457 and parameters: {'iterations': 211, 'depth': 7, 'learning_rate': 0.048617761959653095, 'l2_leaf_reg': 0.7855184718312891}. Best is trial 0 with value: 0.8842288158246457.
[I 2024-10-15 16:45:41,721] Trial 1 finished with value: 0.89585672280139 and parameters: {'iterations': 219, 'depth': 4, 'learning_rate': 0.047438328962724374, 'l2_leaf_reg': 4.614037729709972}. Best is trial 1 with value: 0.89585672280139.
[I 2024-10-15 16:45:44,186] Trial 2 finished with value: 0.8934509489441325 and parameters: {'iterations': 266, 'depth': 7, 'learning_rate': 0.198273289005973, 'l2_leaf_reg': 8.963053335811539}. Best is trial 1 with value: 0.89585672280139.
[I 2024-10-15 16:45:46,584] Trial 3 finished with value: 0.8842822774659181 and parameters: {'iterations': 420, 'depth': 5, 'learning_rate': 0.0519049712688

Best CatBoost params: {'iterations': 178, 'depth': 3, 'learning_rate': 0.26755781320842015, 'l2_leaf_reg': 0.7966229454617894}


In [28]:
# Train the models with the best parameters found
dt_best = DecisionTreeClassifier(**best_dt_params, random_state=42)
xgb_best = XGBClassifier(**best_xgb_params, use_label_encoder=False, eval_metric='logloss', random_state=42)
lgbm_best = LGBMClassifier(**best_lgbm_params, random_state=42)
catboost_best = CatBoostClassifier(**best_catboost_params, verbose=0, random_state=42)

# Cross-validation for evaluation
dt_score = cross_val_score(dt_best, X_train, y_train, cv=cv, scoring='accuracy').mean()
xgb_score = cross_val_score(xgb_best, X_train, y_train, cv=cv, scoring='accuracy').mean()
lgbm_score = cross_val_score(lgbm_best, X_train, y_train, cv=cv, scoring='accuracy').mean()
catboost_score = cross_val_score(catboost_best, X_train, y_train, cv=cv, scoring='accuracy').mean()

print(f"Decision Tree Final Cross-Validation Accuracy: {dt_score:.4f}")
print(f"XGBoost Final Cross-Validation Accuracy: {xgb_score:.4f}")
print(f"LightGBM Final Cross-Validation Accuracy: {lgbm_score:.4f}")
print(f"CatBoost Final Cross-Validation Accuracy: {catboost_score:.4f}")

[LightGBM] [Info] Number of positive: 113, number of negative: 232
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000169 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1667
[LightGBM] [Info] Number of data points in the train set: 345, number of used features: 44
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.327536 -> initscore=-0.719350
[LightGBM] [Info] Start training from score -0.719350
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes